In [1]:

from elftools.elf.elffile import ELFFile
from elftools.dwarf.descriptions import (
    describe_DWARF_expr, set_global_machine_arch)
from elftools.dwarf.locationlists import (
    LocationEntry, LocationExpr, LocationParser)

import posixpath
binFileName = 
filePath = './../../binaries/gnuit/src/gitfm'

# filePath = './../../binaries/c_many/stacktest'


In [2]:
def get_DIE_at_offset(CU, offset):
        for die in CU.iter_DIEs():
            if die.offset == CU.cu_offset+offset:
                return die 
        return None


##TODO FIX CONSTANT TYPE
def get_type_name(CU, offset):#get_DIE_at_offset(CU,attr.value)
    die = get_DIE_at_offset(CU, offset)
    
    if die.tag == 'DW_TAG_const_type':
        return "const"
    
    if die.tag == 'DW_TAG_pointer_type' :
        for _attr in die.attributes.values():
            if _attr.name== "DW_AT_type":
                
                return "*"+get_type_name(CU, _attr.value) 

    elif die.tag =='DW_TAG_subroutine_type':
        

        for _attr in die.attributes.values():
            if _attr.name== "DW_AT_sibling":
                return get_type_name(CU, _attr.value) 
            
            if _attr.name== "DW_AT_type":
                return "*"+get_type_name(CU, _attr.value) 

    for attr in die.attributes.values():
        if attr.name== "DW_AT_name":
            return attr.value.decode("utf-8")

#     print("producing none?")
    
    


In [3]:
from collections import defaultdict
def line_entry_mapping(line_program,CU):
    filename_map = defaultdict(int)

    # The line program, when decoded, returns a list of line program
    # entries. Each entry contains a state, which we'll use to build
    # a reverse mapping of filename -> #entries.
    lp_entries = line_program.get_entries()
    if len(lp_entries)==0:
        return None
    for lpe in lp_entries:
        # We skip LPEs that don't have an associated file.
        # This can happen if instructions in the compiled binary
        # don't correspond directly to any original source file.
        if not lpe.state:# or lpe.state.file == 0
            continue
        filename = lpe_filename(line_program, lpe.state.file,CU)[0]
        filename_map[filename] += 1

    # for filename, lpe_count in filename_map.items():
    #     print("    filename=%s -> %d entries" % (filename, lpe_count))
    return filename_map

def lpe_filename(line_program, file_index, CU):
    
    
    die_dict = {}                    
    for attr in CU.get_top_DIE().attributes.values():
        die_dict[attr.name] = attr
    
    
    compilation_command = die_dict['DW_AT_producer'].value.decode("utf-8")
    print(compilation_command)
    if 'clang' in compilation_command.lower():
        COMPILER_SUBSTRACT = 1
    elif 'gnu' in compilation_command.lower():
        COMPILER_SUBSTRACT = 0
    lp_header = line_program.header
    file_entries = lp_header["file_entry"]
    

    # File and directory indices are 1-indexed.
    file_entry = file_entries[file_index -COMPILER_SUBSTRACT]
    dir_index = file_entry["dir_index"]

    # A dir_index of 0 indicates that no absolute directory was recorded during
    # compilation; return just the basename.
    if dir_index == 0:
        return file_entry.name.decode(),dir_index
    directory = lp_header["include_directory"][dir_index -COMPILER_SUBSTRACT]
    return posixpath.join(directory, file_entry.name).decode(),dir_index

In [4]:
def show_loclist(loclist, dwarfinfo, indent, cu_offset):
    """ Display a location list nicely, decoding the DWARF expressions
        contained within.
    """
    d = []
    for loc_entity in loclist:
        if isinstance(loc_entity, LocationEntry):
            d.append('%s <<%s>>' % (
                loc_entity,
                describe_DWARF_expr(loc_entity.loc_expr, dwarfinfo.structs, cu_offset)))
        else:
            d.append(str(loc_entity))
    return '\n'.join(indent + s for s in d)

In [5]:
# https://github.com/eliben/pyelftools/blob/master/examples/dwarf_location_info.py

LOCATION_SUBSTRACT_FACTOR = 4

from elftools.dwarf.locationlists import LocationParser, LocationExpr
FUNC_PARAMS = {}
def process_file(filename):
    print('Processing file:', filename)
    with open(filename, 'rb') as f:
        elffile = ELFFile(f)

        if not elffile.has_dwarf_info():
            print('  file has no DWARF info')
            return

        # get_dwarf_info returns a DWARFInfo context object, which is the
        # starting point for all DWARF-based processing in pyelftools.
        dwarfinfo = elffile.get_dwarf_info()
        # The location lists are extracted by DWARFInfo from the .debug_loc
        # section, and returned here as a LocationLists object.
        location_lists = dwarfinfo.location_lists()
        

        # This is required for the descriptions module to correctly decode
        # register names contained in DWARF expressions.
        set_global_machine_arch(elffile.get_machine_arch())

        # Create a LocationParser object that parses the DIE attributes and
        # creates objects representing the actual location information.
        loc_parser = LocationParser(location_lists)
        
        section_offset = dwarfinfo.debug_info_sec.global_offset
        # Offset of the .debug_info section in the stream
        


        for CU in dwarfinfo.iter_CUs():

                
            line_program = dwarfinfo.line_program_for_CU(CU)
            filename_map = line_entry_mapping(line_program,CU)
            if filename_map==None:
                continue
            CU_src_file =  list(filename_map.items())[0][0]
            print(CU_src_file)
            CU_dictionary_key = CU_src_file 
            
            FUNC_PARAMS[CU_dictionary_key] = {}
            
            print('  Found a compile unit at offset %s, length %s' % (
                CU.cu_offset, CU['unit_length']))

            # A CU provides a simple API to iterate over all the DIEs in it.
            die_depth = 0
            are_DIEs_of_function = False
            FUNC_name = None
            for DIE in CU.iter_DIEs():
                
                ############################################################
                #############   Prasing Function DIEs start ################
                
                
                if DIE.tag == 'DW_TAG_subprogram':
                    are_DIEs_of_function = True
                    
                    for attr in DIE.attributes.values():
                        if attr.name == "DW_AT_name": #FUNC NAME
                            FUNC_name = attr.value.decode("utf-8")
                            FUNC_PARAMS[CU_dictionary_key][FUNC_name] ={}
                            print("SUBPROGRAM: ",FUNC_name)
                            
                if DIE.tag == 'DW_TAG_formal_parameter' or DIE.tag =='DW_TAG_variable':
                    tags = [attr.name for attr in DIE.attributes.values()]
                    PARAM_name = None
                    if FUNC_name==None:

                        FUNC_name ="global"
                        
                        if FUNC_name not in FUNC_PARAMS[CU_dictionary_key]:
                            FUNC_PARAMS[CU_dictionary_key][FUNC_name]={}
                        
                    if "DW_AT_name" in tags:
                        
                        die_dict = {}
                        
                        for attr in DIE.attributes.values():
                            die_dict[attr.name] = attr
                        
                        PARAM_name = die_dict['DW_AT_name'].value.decode("utf-8")
                        FUNC_PARAMS[CU_dictionary_key][FUNC_name][PARAM_name] = {}
                        var_type = DIE.tag.split('_')[-1]
                        FUNC_PARAMS[CU_dictionary_key][FUNC_name][PARAM_name] = {'type':get_type_name(CU,die_dict['DW_AT_type'].value) , 'kind':var_type}
                        
#                         print(die_dict)
                        # Check if this attribute contains location information
#                         if loc_parser.attribute_has_location(die_dict['DW_AT_location'], CU['version']):
                        if 'DW_AT_location' in die_dict:

                            try:
                                loc = loc_parser.parse_from_attribute(die_dict['DW_AT_location'],
                                                                      CU['version'])
                                
#                                 print(CU_dictionary_key,FUNC_name,PARAM_name)
                                if isinstance(loc, LocationExpr):
                                    loc_info_str = describe_DWARF_expr(loc.loc_expr, dwarfinfo.structs, CU.cu_offset)
                                    offset_temp = (loc_info_str.split('-')[-1]).split(')')[0]
#                                     print('1a ',loc_info_str, offset_temp)
#                                     print('1b ', PARAM_name,loc_info_str, int(offset_temp)-LOCATION_SUBSTRACT_FACTOR)
                                    FUNC_PARAMS[CU_dictionary_key][FUNC_name][PARAM_name]["location"]= loc_info_str

                                elif isinstance(loc, list):
                                    print(PARAM_name,show_loclist(loc,dwarfinfo,'      ', CU.cu_offset))
                                    FUNC_PARAMS[CU_dictionary_key][FUNC_name][PARAM_name]["location"]= show_loclist(loc,
                                                       dwarfinfo,'      ', CU.cu_offset)
                            except:

                                print("ERROR",DIE)
                                pass

                ###############################################
                #############  parsing  Function DIEs ends ################
                


                
                if DIE.is_null(): #https://chromium.googlesource.com/chromiumos/third_party/pyelftools/+/25a77f7738d7fe824f2ed4d33a123136b9d8e88a/scripts/readelf.py
                    are_DIEs_of_function = False
                    FUNC_name = None
                    
                    die_depth -= 1
                    continue
                if DIE.has_children:
                    die_depth += 1
                    

process_file(filePath)

Processing file: ./../../binaries/gnuit/src/gitfm
GNU C17 11.3.0 -mtune=generic -march=x86-64 -g -gdwarf -ffunction-sections -fdata-sections -fasynchronous-unwind-tables -fstack-protector-strong -fstack-clash-protection -fcf-protection
GNU C17 11.3.0 -mtune=generic -march=x86-64 -g -gdwarf -ffunction-sections -fdata-sections -fasynchronous-unwind-tables -fstack-protector-strong -fstack-clash-protection -fcf-protection
GNU C17 11.3.0 -mtune=generic -march=x86-64 -g -gdwarf -ffunction-sections -fdata-sections -fasynchronous-unwind-tables -fstack-protector-strong -fstack-clash-protection -fcf-protection
GNU C17 11.3.0 -mtune=generic -march=x86-64 -g -gdwarf -ffunction-sections -fdata-sections -fasynchronous-unwind-tables -fstack-protector-strong -fstack-clash-protection -fcf-protection
GNU C17 11.3.0 -mtune=generic -march=x86-64 -g -gdwarf -ffunction-sections -fdata-sections -fasynchronous-unwind-tables -fstack-protector-strong -fstack-clash-protection -fcf-protection
GNU C17 11.3.0 -mtun

SUBPROGRAM:  tty_resize
SUBPROGRAM:  tty_get_previous_key_seq
SUBPROGRAM:  tty_key_print_async
SUBPROGRAM:  tty_get_key
SUBPROGRAM:  tty_key_print
SUBPROGRAM:  tty_key_search
SUBPROGRAM:  tty_key_search_restart
SUBPROGRAM:  tty_key_list_insert
SUBPROGRAM:  tty_key_list_insert_sequence
SUBPROGRAM:  tty_getc
SUBPROGRAM:  tty_extract_key
SUBPROGRAM:  tty_defaults
SUBPROGRAM:  tty_restore
SUBPROGRAM:  tty_save
SUBPROGRAM:  tty_cursor
SUBPROGRAM:  tty_beep
SUBPROGRAM:  tty_colors
SUBPROGRAM:  tty_reversevid
SUBPROGRAM:  tty_brightness
SUBPROGRAM:  tty_background
SUBPROGRAM:  tty_foreground
SUBPROGRAM:  tty_get_cursor
SUBPROGRAM:  tty_goto
SUBPROGRAM:  tty_io_colors
SUBPROGRAM:  tty_io_reversevid
SUBPROGRAM:  tty_io_brightness
SUBPROGRAM:  tty_io_background
SUBPROGRAM:  tty_io_foreground
SUBPROGRAM:  tty_io_goto
SUBPROGRAM:  tty_touch
SUBPROGRAM:  tty_fill
SUBPROGRAM:  tty_clear
SUBPROGRAM:  tty_read
SUBPROGRAM:  tty_putc
SUBPROGRAM:  tty_puts
SUBPROGRAM:  tty_writes
SUBPROGRAM:  tty_update


SUBPROGRAM:  panel_deallocate_patterns
SUBPROGRAM:  panel_parse_patterns
SUBPROGRAM:  panel_act_BIN_PACKING
SUBPROGRAM:  pack_compare_fn
SUBPROGRAM:  panel_act_CASE
SUBPROGRAM:  panel_case_rename
SUBPROGRAM:  panel_act_CMPDIR
SUBPROGRAM:  panel_act_COMPARE
SUBPROGRAM:  panel_compare
SUBPROGRAM:  panel_act_REGET
SUBPROGRAM:  panel_act_CHDIR
SUBPROGRAM:  panel_act_MOVE
SUBPROGRAM:  panel_act_MKDIR
SUBPROGRAM:  panel_mkdirs
SUBPROGRAM:  panel_isdir
SUBPROGRAM:  panel_act_DELETE
SUBPROGRAM:  panel_act_COPY
SUBPROGRAM:  panel_act_ENTER
SUBPROGRAM:  panel_find_index
SUBPROGRAM:  panel_move
SUBPROGRAM:  panel_copy
SUBPROGRAM:  panel_percent
SUBPROGRAM:  panel_unlink
SUBPROGRAM:  panel_warning
SUBPROGRAM:  same_file
SUBPROGRAM:  canceled
SUBPROGRAM:  panel_get_path
SUBPROGRAM:  panel_unselect_all
SUBPROGRAM:  panel_select_all
SUBPROGRAM:  panel_set_focus
SUBPROGRAM:  panel_update
SUBPROGRAM:  panel_update_frame
SUBPROGRAM:  panel_update_entry
SUBPROGRAM:  panel_get_reserved_characters
SUBPROGR

GNU C17 11.3.0 -mtune=generic -march=x86-64 -g -gdwarf -ffunction-sections -fdata-sections -fasynchronous-unwind-tables -fstack-protector-strong -fstack-clash-protection -fcf-protection
GNU C17 11.3.0 -mtune=generic -march=x86-64 -g -gdwarf -ffunction-sections -fdata-sections -fasynchronous-unwind-tables -fstack-protector-strong -fstack-clash-protection -fcf-protection
GNU C17 11.3.0 -mtune=generic -march=x86-64 -g -gdwarf -ffunction-sections -fdata-sections -fasynchronous-unwind-tables -fstack-protector-strong -fstack-clash-protection -fcf-protection
GNU C17 11.3.0 -mtune=generic -march=x86-64 -g -gdwarf -ffunction-sections -fdata-sections -fasynchronous-unwind-tables -fstack-protector-strong -fstack-clash-protection -fcf-protection
GNU C17 11.3.0 -mtune=generic -march=x86-64 -g -gdwarf -ffunction-sections -fdata-sections -fasynchronous-unwind-tables -fstack-protector-strong -fstack-clash-protection -fcf-protection
GNU C17 11.3.0 -mtune=generic -march=x86-64 -g -gdwarf -ffunction-sect

GNU C17 11.3.0 -mtune=generic -march=x86-64 -g -O2 -fasynchronous-unwind-tables -fstack-protector-strong -fstack-clash-protection -fcf-protection
GNU C17 11.3.0 -mtune=generic -march=x86-64 -g -O2 -fasynchronous-unwind-tables -fstack-protector-strong -fstack-clash-protection -fcf-protection
GNU C17 11.3.0 -mtune=generic -march=x86-64 -g -O2 -fasynchronous-unwind-tables -fstack-protector-strong -fstack-clash-protection -fcf-protection
GNU C17 11.3.0 -mtune=generic -march=x86-64 -g -O2 -fasynchronous-unwind-tables -fstack-protector-strong -fstack-clash-protection -fcf-protection
GNU C17 11.3.0 -mtune=generic -march=x86-64 -g -O2 -fasynchronous-unwind-tables -fstack-protector-strong -fstack-clash-protection -fcf-protection
GNU C17 11.3.0 -mtune=generic -march=x86-64 -g -O2 -fasynchronous-unwind-tables -fstack-protector-strong -fstack-clash-protection -fcf-protection
GNU C17 11.3.0 -mtune=generic -march=x86-64 -g -O2 -fasynchronous-unwind-tables -fstack-protector-strong -fstack-clash-prote

In [6]:
FUNC_PARAMS['misc.c']['get_const_var']


{'var_name': {'type': '*char',
  'kind': 'parameter',
  'location': '(DW_OP_fbreg: -56)'},
 'options': {'type': '**char',
  'kind': 'parameter',
  'location': '(DW_OP_fbreg: -64)'},
 'options_no': {'type': 'int',
  'kind': 'parameter',
  'location': '(DW_OP_fbreg: -68)'},
 'default_value': {'type': 'int',
  'kind': 'parameter',
  'location': '(DW_OP_fbreg: -72)'},
 'i': {'type': 'int', 'kind': 'variable', 'location': '(DW_OP_fbreg: -36)'},
 'data': {'type': '*char',
  'kind': 'variable',
  'location': '(DW_OP_fbreg: -32)'}}

In [7]:
#!/usr/bin/env python3

import sys,os
from elftools.elf.elffile import ELFFile
from elftools.elf.segments import Segment






In [8]:

fh = open(filePath, 'rb')
bin_bytearray = bytearray(fh.read())

In [9]:
# https://www.capstone-engine.org/lang_python.html



from capstone import *

from capstone.x86 import *


address_inst = {}
with open(filePath, 'rb') as f:
    elf = ELFFile(f)
    dwarfinfo = elf.get_dwarf_info()
    aranges = dwarfinfo.get_aranges()
    print(len(aranges.entries))
    for arange in aranges.entries:
        print(arange)
    for arange in aranges.entries:

        entry = arange.begin_addr
        exit  = arange.begin_addr + arange.length
        ops = bin_bytearray[entry: exit]

        md = Cs(CS_ARCH_X86, CS_MODE_64)
        md.detail = True
        for inst in md.disasm(ops, entry):

            address_inst[hex(inst.address)] = inst


            print('\n'*3)
            print(inst.address, inst.mnemonic+"  "+inst.op_str)
            (regs_read, regs_write) = inst.regs_access()



341
ARangeEntry(begin_addr=20192, length=5, info_offset=76698, unit_length=60, version=2, address_size=8, segment_size=0)
ARangeEntry(begin_addr=20441, length=72, info_offset=0, unit_length=460, version=2, address_size=8, segment_size=0)
ARangeEntry(begin_addr=20513, length=25, info_offset=0, unit_length=460, version=2, address_size=8, segment_size=0)
ARangeEntry(begin_addr=20538, length=813, info_offset=0, unit_length=460, version=2, address_size=8, segment_size=0)
ARangeEntry(begin_addr=21351, length=315, info_offset=0, unit_length=460, version=2, address_size=8, segment_size=0)
ARangeEntry(begin_addr=21666, length=298, info_offset=0, unit_length=460, version=2, address_size=8, segment_size=0)
ARangeEntry(begin_addr=21964, length=147, info_offset=0, unit_length=460, version=2, address_size=8, segment_size=0)
ARangeEntry(begin_addr=22111, length=94, info_offset=0, unit_length=460, version=2, address_size=8, segment_size=0)
ARangeEntry(begin_addr=22205, length=729, info_offset=0, unit_





61439 mov  dword ptr [rax + 0x10], 0x11




61446 nop  




61447 pop  rbp




61448 ret  




61449 endbr64  




61453 push  rbp




61454 mov  rbp, rsp




61457 sub  rsp, 0x10




61461 mov  rax, qword ptr [rip + 0x223f4]




61468 mov  rdx, qword ptr [rax + 0x18]




61472 mov  rax, qword ptr [rip + 0x223e9]




61479 mov  rax, qword ptr [rax + 0x38]




61483 cmp  rdx, rax




61486 jae  0xf0ac




61488 mov  rax, qword ptr [rip + 0x223d9]




61495 mov  rax, qword ptr [rax + 0x18]




61499 mov  qword ptr [rbp - 8], rax




61503 mov  eax, 0




61508 call  0xe655




61513 mov  rax, qword ptr [rbp - 8]




61517 mov  qword ptr [rbp - 0x10], rax




61521 jmp  0xf08d




61523 mov  rax, qword ptr [rip + 0x223b6]




61530 mov  rdx, qword ptr [rax + 0x58]




61534 mov  rax, qword ptr [rbp - 0x10]




61538 add  rax, rdx




61541 movzx  eax, byte ptr [rax]




61544 movsx  eax, al




61547 mov  edi, eax




61549 call  0x4be0




61554 mov  edx, eax




61556 mov  rax, qwor





93063 lea  rdx, [rip + 0x11a50]




93070 mov  rsi, rdx




93073 mov  rdi, rax




93076 call  0x4af0




93081 test  eax, eax




93083 sete  al




93086 movzx  eax, al




93089 mov  dword ptr [rbp - 0x28], eax




93092 mov  rax, qword ptr [rbp - 0x38]




93096 mov  rax, qword ptr [rax + 0x78]




93100 add  rax, 1




93104 mov  rdi, rax




93107 call  0x24650




93112 mov  qword ptr [rbp - 0x10], rax




93116 mov  rax, qword ptr [rbp - 0x38]




93120 mov  rdx, qword ptr [rax + 0x18]




93124 mov  rax, qword ptr [rbp - 0x10]




93128 mov  rsi, rdx




93131 mov  rdi, rax




93134 call  0x4870




93139 mov  rcx, qword ptr [rbp - 0x20]




93143 mov  rax, qword ptr [rbp - 0x38]




93147 mov  edx, 1




93152 mov  rsi, rcx




93155 mov  rdi, rax




93158 mov  eax, 0




93163 call  0x12238




93168 test  eax, eax




93170 jne  0x16c46




93172 cmp  dword ptr [rbp - 0x28], 0




93176 je  0x16c1c




93178 mov  rax, qword ptr [rbp - 0x38]




93182 mov  rdi, rax








123177 movzx  eax, byte ptr [rax]




123180 cmp  al, 0x2e




123182 jne  0x1e1ab




123184 mov  rax, qword ptr [rbp - 8]




123188 add  rax, 1




123192 movzx  eax, byte ptr [rax]




123195 cmp  al, 0x2e




123197 jne  0x1e1ab




123199 mov  rax, qword ptr [rbp - 8]




123203 add  rax, 2




123207 movzx  eax, byte ptr [rax]




123210 cmp  al, 0x2f




123212 je  0x1e15d




123214 mov  rax, qword ptr [rbp - 8]




123218 add  rax, 2




123222 movzx  eax, byte ptr [rax]




123225 test  al, al




123227 jne  0x1e1ab




123229 mov  rax, qword ptr [rbp - 0x10]




123233 sub  rax, 1




123237 cmp  qword ptr [rbp - 0x18], rax




123241 je  0x1e187




123243 sub  qword ptr [rbp - 0x10], 2




123248 jmp  0x1e177




123250 sub  qword ptr [rbp - 0x10], 1




123255 mov  rax, qword ptr [rbp - 0x10]




123259 movzx  eax, byte ptr [rax]




123262 cmp  al, 0x2f




123264 jne  0x1e172




123266 add  qword ptr [rbp - 0x10], 1




123271 add  qword ptr [rbp - 8], 2




1232

In [10]:
from collections import defaultdict
import posixpath


In [11]:
addr_lineProgram ={}
addr_sourceFile = {}
with open(filePath, 'rb') as f:
    elffile = ELFFile(f)

    if not elffile.has_dwarf_info():
        print('  file has no DWARF info')
        exit(0)

    dwarfinfo = elffile.get_dwarf_info()
    for CU in dwarfinfo.iter_CUs():
#         print(CU.get_top_DIE()['DW_AT_comp_dir'])
        CU_DIR_PATH = None
        CU_FILENAME = None
        for attr in CU.get_top_DIE().attributes.values():
            if attr.name == 'DW_AT_comp_dir':
                CU_DIR_PATH = attr.value.decode("utf-8")
            if attr.name == 'DW_AT_name':
                CU_FILENAME = attr.value.decode("utf-8")
            
        print('  Found a compile unit at offset %s, length %s' % (
            CU.cu_offset, CU['unit_length']))

        # Every compilation unit in the DWARF information may or may not
        # have a corresponding line program in .debug_line.
        line_program = dwarfinfo.line_program_for_CU(CU)
        if line_program is None:
            print('  DWARF info is missing a line program for this CU')
            continue

        for line_entry in line_program.get_entries():
            real_source_path = None
            if line_entry.state!=None:
                    addr_lineProgram[hex(line_entry.state.address)] = line_entry

                    src_filename_from_lineentry, dir_index = (lpe_filename (line_program, line_entry.state.file,CU))
                    
                    if src_filename_from_lineentry == CU_FILENAME:
                        real_source_path = os.path.join(CU_DIR_PATH,CU_FILENAME)
                    else:
                        if '/' in src_filename_from_lineentry:
                            real_source_path = src_filename_from_lineentry
                        elif dir_index==0:
                            real_source_path = os.path.join(CU_DIR_PATH,src_filename_from_lineentry)

                    addr_sourceFile [hex(line_entry.state.address)] = real_source_path


        


  Found a compile unit at offset 0, length 10410
GNU C17 11.3.0 -mtune=generic -march=x86-64 -g -gdwarf -ffunction-sections -fdata-sections -fasynchronous-unwind-tables -fstack-protector-strong -fstack-clash-protection -fcf-protection
GNU C17 11.3.0 -mtune=generic -march=x86-64 -g -gdwarf -ffunction-sections -fdata-sections -fasynchronous-unwind-tables -fstack-protector-strong -fstack-clash-protection -fcf-protection
GNU C17 11.3.0 -mtune=generic -march=x86-64 -g -gdwarf -ffunction-sections -fdata-sections -fasynchronous-unwind-tables -fstack-protector-strong -fstack-clash-protection -fcf-protection
GNU C17 11.3.0 -mtune=generic -march=x86-64 -g -gdwarf -ffunction-sections -fdata-sections -fasynchronous-unwind-tables -fstack-protector-strong -fstack-clash-protection -fcf-protection
GNU C17 11.3.0 -mtune=generic -march=x86-64 -g -gdwarf -ffunction-sections -fdata-sections -fasynchronous-unwind-tables -fstack-protector-strong -fstack-clash-protection -fcf-protection
GNU C17 11.3.0 -mtune

GNU C17 11.3.0 -mtune=generic -march=x86-64 -g -gdwarf -ffunction-sections -fdata-sections -fasynchronous-unwind-tables -fstack-protector-strong -fstack-clash-protection -fcf-protection
GNU C17 11.3.0 -mtune=generic -march=x86-64 -g -gdwarf -ffunction-sections -fdata-sections -fasynchronous-unwind-tables -fstack-protector-strong -fstack-clash-protection -fcf-protection
GNU C17 11.3.0 -mtune=generic -march=x86-64 -g -gdwarf -ffunction-sections -fdata-sections -fasynchronous-unwind-tables -fstack-protector-strong -fstack-clash-protection -fcf-protection
GNU C17 11.3.0 -mtune=generic -march=x86-64 -g -gdwarf -ffunction-sections -fdata-sections -fasynchronous-unwind-tables -fstack-protector-strong -fstack-clash-protection -fcf-protection
GNU C17 11.3.0 -mtune=generic -march=x86-64 -g -gdwarf -ffunction-sections -fdata-sections -fasynchronous-unwind-tables -fstack-protector-strong -fstack-clash-protection -fcf-protection
GNU C17 11.3.0 -mtune=generic -march=x86-64 -g -gdwarf -ffunction-sect

GNU C17 11.3.0 -mtune=generic -march=x86-64 -g -O2 -fasynchronous-unwind-tables -fstack-protector-strong -fstack-clash-protection -fcf-protection
GNU C17 11.3.0 -mtune=generic -march=x86-64 -g -O2 -fasynchronous-unwind-tables -fstack-protector-strong -fstack-clash-protection -fcf-protection
GNU C17 11.3.0 -mtune=generic -march=x86-64 -g -O2 -fasynchronous-unwind-tables -fstack-protector-strong -fstack-clash-protection -fcf-protection
GNU C17 11.3.0 -mtune=generic -march=x86-64 -g -O2 -fasynchronous-unwind-tables -fstack-protector-strong -fstack-clash-protection -fcf-protection
GNU C17 11.3.0 -mtune=generic -march=x86-64 -g -O2 -fasynchronous-unwind-tables -fstack-protector-strong -fstack-clash-protection -fcf-protection
GNU C17 11.3.0 -mtune=generic -march=x86-64 -g -O2 -fasynchronous-unwind-tables -fstack-protector-strong -fstack-clash-protection -fcf-protection
GNU C17 11.3.0 -mtune=generic -march=x86-64 -g -O2 -fasynchronous-unwind-tables -fstack-protector-strong -fstack-clash-prote

In [12]:
# print(addr_lineProgram)
# address_inst

def getSource(sourceFilePath, row , col):
    sourceFile = open(sourceFilePath, "r")
    fileContent = sourceFile.readlines()
    row_content =  fileContent[row-1]
    row_content = row_content[:(col-1)] + '|'+row_content[(col-1)]+'|' +row_content[col:]
    
    return row_content


In [13]:

# FUNCTION_DECL
# https://stackoverflow.com/questions/43460605/function-boundary-identification-using-libclang
# https://eli.thegreenplace.net/2011/07/03/parsing-c-in-python-with-clang


import clang.cindex



def get_all_var_types(source_path):
    srcFileName = source_path.split('/')[-1]

    function_boundary_by_name = {}
    idx = clang.cindex.Index.create()
    tu = idx.parse(source_path)
    
    for f in tu.cursor.walk_preorder():
        if f.kind == clang.cindex.CursorKind.VAR_DECL:
            # print(dir(f))
            print(f.extent.start.file.name)
            originFileName = f.extent.start.file.name.split('/')[-1]
            print(originFileName)
            print(f.displayname)
            print(f.type.spelling)
            print(f.extent.start.line,f.extent.start.column)
            print('\n')
            
            

   

def get_all_function_types(source_path):
    function_boundary_by_name = {}
    idx = clang.cindex.Index.create()
    tu = idx.parse(source_path)
    
    for f in tu.cursor.walk_preorder():
        if f.kind == clang.cindex.CursorKind.FUNCTION_DECL:
            # print(dir(f))
            print(f.displayname)
            print('function name: ',( f.spelling))
            print('Returns: ',(f.result_type.spelling))
            
            
            arg_len = len(list(f.type.argument_types()))
            if arg_len>0:
                arg_types = list(f.type.argument_types())
                for arg_type in arg_types:
                    print('arg_type:',arg_type.spelling)
                args = list(f.get_arguments())
                for arg in args:
                    print('arg:',arg.spelling)


            print("\n\n\n")

            
def get_function_boundaries(source_path):
    
    function_boundary_by_name = {}
    idx = clang.cindex.Index.create()
    tu = idx.parse(source_path)
    
    for f in tu.cursor.walk_preorder():
        if f.kind == clang.cindex.CursorKind.FUNCTION_DECL:

            function_name = f.displayname.split('(')[0]
            function_boundary_by_name[function_name]={}
            function_boundary_by_name[function_name] = { 'src_path':f.extent.start.file.name,
                              'src_file':f.extent.start.file.name.split('/')[-1],
                              'start_line':f.extent.start.line,
                              'start_col':f.extent.start.column,
                              'end_line':f.extent.end.line,
                              'end_col':f.extent.end.column}
    return function_boundary_by_name

def get_containing_function(source_file_path, line, col=0):
    function_boundary_by_name = get_function_boundaries(source_file_path)
    
    for function_name, item in function_boundary_by_name.items():
        if item['src_path'] == source_file_path:
            if line>= item['start_line'] and line<= item['end_line']:
                return function_name
        



In [ ]:
REGISTER_SUBSTRACT_FACTOR = -4

with open('gitfm.s', 'w') as outFile:
    # outFile.write('file contents\n')
    lastSource = ""
    for address in address_inst:
        inst = address_inst[address]
        instrctionCode = (address+":\t"+ inst.mnemonic+" "+inst.op_str).ljust(45)

        OFFSET = None
        if len(inst.operands) > 0 :
            c=-1
            for o in inst.operands:
                c += 1
                if o.type == CS_OP_MEM:
                    print("\t\toperands[%u].type: MEM" %c)
                    if o.value.mem.base != 0:
                        print("\t\t\toperands[%u].mem.base: REG = %s" \
                            %(c, inst.reg_name(o.value.mem.base)))
                    if o.value.mem.index != 0:
                        print("\t\t\toperands[%u].mem.index: REG = %s" \
                            %(c, inst.reg_name(o.value.mem.index)))
                    if o.value.mem.disp != 0:
                        print("\t\t\toperands[%u].mem.disp: 0x%x" \
                            %(c, o.value.mem.disp))
                        OFFSET = o.value.mem.disp
                    print(hex(o.value.mem.disp),o.value.mem.disp)
                    
        
        if address in addr_lineProgram:
            
            srcFilePath = addr_sourceFile[address] 
            if srcFilePath!=lastSource:
                outFile.write("\n"+ '#'*100+"\n"+ srcFilePath.rjust(45) +'\n'+'#'*100+ "\n\n")
                lastSource = srcFilePath
            print("add",address)
            

            sourceCode = getSource(srcFilePath,addr_lineProgram[address].state.line, addr_lineProgram[address].state.column)
            function_name = get_containing_function(srcFilePath ,addr_lineProgram[address].state.line , addr_lineProgram[address].state.column)


            if '\n' not in  sourceCode:
                sourceCode+=sourceCode+"\n"
            outFile.write(instrctionCode+"#"+ sourceCode  )
            print(instrctionCode+"#"+ sourceCode)

            
        else:
            
            outFile.write(instrctionCode+ '\n'  )
            print(instrctionCode)
        if OFFSET:
            outFile.write("MEMORY OFFSET:     "+str(hex(OFFSET))+"     "+str(OFFSET)+ "  >>"+str(OFFSET-REGISTER_SUBSTRACT_FACTOR)+'\n\n')
            pass

add 0x4ee0
0x4ee0:	call 0x4810                          #    |a|bort ();

add 0x4fd9
0x4fd9:	endbr64                              #|{|

0x4fdd:	push rbp                             
0x4fde:	mov rbp, rsp                         
		operands[1].type: MEM
			operands[1].mem.base: REG = rip
			operands[1].mem.disp: 0x2b9f5
0x2b9f5 178677
add 0x4fe1
0x4fe1:	mov eax, dword ptr [rip + 0x2b9f5]   #    if (tty_lines |>|= 7)

add 0x4fe7
0x4fe7:	cmp eax, 6                           #    if |(|tty_lines >= 7)

0x4fea:	jle 0x501a                           
		operands[1].type: MEM
			operands[1].mem.base: REG = rip
			operands[1].mem.disp: 0x2a036
0x2a036 172086
add 0x4fec
0x4fec:	mov eax, dword ptr [rip + 0x2a036]   #	if (|t|wo_panel_mode)

add 0x4ff2
0x4ff2:	test eax, eax                        #	if |(|two_panel_mode)

0x4ff4:	je 0x5008                            
		operands[1].type: MEM
			operands[1].mem.base: REG = rip
			operands[1].mem.disp: 0x2b9e4
0x2b9e4 178660
add 0x4ff6
0x4ff6:	mov eax, d

0x510a:	test eax, eax                        #	if |(|two_panel_mode)

0x510c:	je 0x5234                            
		operands[1].type: MEM
			operands[1].mem.base: REG = rip
			operands[1].mem.disp: 0x2b8c8
0x2b8c8 178376
add 0x5112
0x5112:	mov eax, dword ptr [rip + 0x2b8c8]   #	    int right_panel_columns = (tty_columns |>|> 1);

add 0x5118
0x5118:	sar eax, 1                           #	    int |r|ight_panel_columns = (tty_columns >> 1);

		operands[0].type: MEM
			operands[0].mem.base: REG = rbp
			operands[0].mem.disp: 0x-18
-0x18 -24
0x511a:	mov dword ptr [rbp - 0x18], eax      
		operands[1].type: MEM
			operands[1].mem.base: REG = rip
			operands[1].mem.disp: 0x2b8bd
0x2b8bd 178365
add 0x511d
0x511d:	mov eax, dword ptr [rip + 0x2b8bd]   #	    int left_panel_columns = right_panel_columns + (tty_columns |&| 1);

0x5123:	and eax, 1                           
0x5126:	mov edx, eax                         
		operands[1].type: MEM
			operands[1].mem.base: REG = rbp
			operands[1].mem.d

0x5271:	mov eax, dword ptr [rip + 0x2b765]   #	    panel_resize(dst_panel, 0, 1, tty_lines |-| 3, tty_columns);

0x5277:	sub eax, 3                           
add 0x527a
0x527a:	movsxd rdx, eax                      #	    |p|anel_resize(dst_panel, 0, 1, tty_lines - 3, tty_columns);

		operands[1].type: MEM
			operands[1].mem.base: REG = rip
			operands[1].mem.disp: 0x2b694
0x2b694 177812
0x527d:	mov rax, qword ptr [rip + 0x2b694]   
0x5284:	mov r8, rcx                          
0x5287:	mov rcx, rdx                         
0x528a:	mov edx, 1                           
0x528f:	mov esi, 0                           
0x5294:	mov rdi, rax                         
0x5297:	call 0x11348                         
0x529c:	jmp 0x52e6                           
		operands[1].type: MEM
			operands[1].mem.base: REG = rip
			operands[1].mem.disp: 0x2b66b
0x2b66b 177771
add 0x529e
0x529e:	mov rax, qword ptr [rip + 0x2b66b]   #	|p|anel_resize(src_panel, 0x10000, 0x10000, 2, 80);

0x52a5:	mov r8d, 0x50   

0x53e9:	mov eax, dword ptr [rip + 0x2b4f1]   #    if (current_mode |=|= GIT_SCREEN_MODE)

add 0x53ef
0x53ef:	test eax, eax                        #    if |(|current_mode == GIT_SCREEN_MODE)

0x53f1:	jne 0x5449                           
add 0x53f3
0x53f3:	mov eax, 0                           #	if (!|p|anels_can_be_displayed())

0x53f8:	call 0x4fd9                          
add 0x53fd
0x53fd:	test eax, eax                        #	if |(|!panels_can_be_displayed())

0x53ff:	jne 0x5415                           
add 0x5401
0x5401:	mov eax, 0                           #	    |t|ty_defaults();

0x5406:	call 0xc083                          
add 0x540b
0x540b:	mov eax, 0                           #	    |t|ty_clear();

0x5410:	call 0xb8a5                          
add 0x5415
0x5415:	mov eax, 0                           #	|t|itle_update();

0x541a:	call 0x1c9f4                         
		operands[1].type: MEM
			operands[1].mem.base: REG = rip
			operands[1].mem.disp: 0x2b4ea
0x2b4ea 177386
add 

0x5576:	mov edi, 1                           #	|s|leep(1);

0x557b:	call 0x4e70                          
add 0x5580
0x5580:	jmp 0x558c                           #    |{|

add 0x5582
0x5582:	mov eax, 0                           #	|t|ty_beep();

0x5587:	call 0xbfbf                          
		operands[0].type: MEM
			operands[0].mem.base: REG = rbp
			operands[0].mem.disp: 0x-28
-0x28 -40
add 0x558c
0x558c:	cmp qword ptr [rbp - 0x28], 0        #    if |(|status_message)

0x5591:	je 0x55ab                            
		operands[1].type: MEM
			operands[1].mem.base: REG = rbp
			operands[1].mem.disp: 0x-28
-0x28 -40
add 0x5593
0x5593:	mov rax, qword ptr [rbp - 0x28]      #	|s|tatus(status_message, STATUS_OK, STATUS_CENTERED);

0x5597:	mov edx, 0                           
0x559c:	mov esi, 0                           
0x55a1:	mov rdi, rax                         
0x55a4:	call 0x107d0                         
0x55a9:	jmp 0x55b5                           
add 0x55ab
0x55ab:	mov eax, 0       

...

0x79fe:	mov dword ptr [rbp - 0x134], 1       #		ansi_colors |=| ON;

add 0x7a08
0x7a08:	jmp 0x7a67                           #		|b|reak;

		operands[0].type: MEM
			operands[0].mem.base: REG = rbp
			operands[0].mem.disp: 0x-134
-0x134 -308
add 0x7a0a
0x7a0a:	mov dword ptr [rbp - 0x134], 0       #		ansi_colors |=| OFF;

add 0x7a14
0x7a14:	jmp 0x7a67                           #		|b|reak;

		operands[0].type: MEM
			operands[0].mem.base: REG = rbp
			operands[0].mem.disp: 0x-130
-0x130 -304
add 0x7a16
0x7a16:	mov dword ptr [rbp - 0x130], 0       #		use_last_screen_character |=| OFF;

add 0x7a20
0x7a20:	jmp 0x7a67                           #		|b|reak;

		operands[0].type: MEM
			operands[0].mem.base: REG = rbp
			operands[0].mem.disp: 0x-140
-0x140 -320
add 0x7a22
0x7a22:	mov dword ptr [rbp - 0x140], 1       #		output_final_path |=| ON;

add 0x7a2c
0x7a2c:	jmp 0x7a67                           #		|b|reak;

add 0x7a2e
0x7a2e:	mov eax, 1                           #		return |1|;

0x7a33:	jmp 

0x7b81:	mov edi, 0xa                         #    |p|rintf("\n");

0x7b86:	call 0x47d0                          
		operands[1].type: MEM
			operands[1].mem.base: REG = rip
			operands[1].mem.disp: 0x1f7e2
0x1f7e2 128994
add 0x7b8b
0x7b8b:	lea r9, [rip + 0x1f7e2]              #    |p|rintf("%s %s (%s), %s %s\n",

		operands[1].type: MEM
			operands[1].mem.base: REG = rip
			operands[1].mem.disp: 0x1f7e7
0x1f7e7 128999
0x7b92:	lea r8, [rip + 0x1f7e7]              
		operands[1].type: MEM
			operands[1].mem.base: REG = rip
			operands[1].mem.disp: 0x1f7e9
0x1f7e9 129001
0x7b99:	lea rax, [rip + 0x1f7e9]             
0x7ba0:	mov rcx, rax                         
		operands[1].type: MEM
			operands[1].mem.base: REG = rip
			operands[1].mem.disp: 0x1f5b3
0x1f5b3 128435
0x7ba3:	lea rax, [rip + 0x1f5b3]             
0x7baa:	mov rdx, rax                         
		operands[1].type: MEM
			operands[1].mem.base: REG = rip
			operands[1].mem.disp: 0x1f749
0x1f749 128841
0x7bad:	lea rax, [rip + 0x1f

0x7d6f:	cmp qword ptr [rbp - 0xc8], 0        #    if |(|temporary_directory == NULL)

0x7d77:	jne 0x7d87                           
		operands[1].type: MEM
			operands[1].mem.base: REG = rip
			operands[1].mem.disp: 0x1f6c7
0x1f6c7 128711
add 0x7d79
0x7d79:	lea rax, [rip + 0x1f6c7]             #	temporary_directory |=| "/tmp";

		operands[0].type: MEM
			operands[0].mem.base: REG = rbp
			operands[0].mem.disp: 0x-c8
-0xc8 -200
0x7d80:	mov qword ptr [rbp - 0xc8], rax      
		operands[1].type: MEM
			operands[1].mem.base: REG = rbp
			operands[1].mem.disp: 0x-c8
-0xc8 -200
add 0x7d87
0x7d87:	mov rax, qword ptr [rbp - 0xc8]      #    stdout_log_name = xmalloc(32 + |s|trlen(temporary_directory) + 1);

0x7d8e:	mov rdi, rax                         
0x7d91:	call 0x4960                          
add 0x7d96
0x7d96:	add rax, 0x21                        #    stdout_log_name = |x|malloc(32 + strlen(temporary_directory) + 1);

0x7d9a:	mov rdi, rax                         
0x7d9d:	call 0x24650      

0x7eed:	mov esi, 0                           #	UseLastScreenChar = |g|et_flag_var("UseLastScreenChar",  OFF);

		operands[1].type: MEM
			operands[1].mem.base: REG = rip
			operands[1].mem.disp: 0x1f584
0x1f584 128388
0x7ef2:	lea rax, [rip + 0x1f584]             
0x7ef9:	mov rdi, rax                         
0x7efc:	call 0x1de4c                         
		operands[0].type: MEM
			operands[0].mem.base: REG = rip
			operands[0].mem.disp: 0x289e5
0x289e5 166373
add 0x7f01
0x7f01:	mov dword ptr [rip + 0x289e5], eax   #	UseLastScreenChar |=| get_flag_var("UseLastScreenChar",  OFF);

0x7f07:	jmp 0x7f13                           
		operands[0].type: MEM
			operands[0].mem.base: REG = rip
			operands[0].mem.disp: 0x289d9
0x289d9 166361
add 0x7f09
0x7f09:	mov dword ptr [rip + 0x289d9], 0     #	UseLastScreenChar |=| OFF;

		operands[1].type: MEM
			operands[1].mem.base: REG = rip
			operands[1].mem.disp: 0x289d3
0x289d3 166355
add 0x7f13
0x7f13:	mov eax, dword ptr [rip + 0x289d3]   #    |t|ty_se

0x8058:	cmp dword ptr [rbp - 0x114], 0x800   #    if |(|keys == MAX_KEYS)

0x8062:	jne 0x808b                           
		operands[1].type: MEM
			operands[1].mem.base: REG = rip
			operands[1].mem.disp: 0x2886d
0x2886d 165997
add 0x8064
0x8064:	mov rdx, qword ptr [rip + 0x2886d]   #	|f|printf(stderr, "%s: too many key sequences; only %d are allowed.\n",

		operands[1].type: MEM
			operands[1].mem.base: REG = rip
			operands[1].mem.disp: 0x2884e
0x2884e 165966
0x806b:	mov rax, qword ptr [rip + 0x2884e]   
0x8072:	mov ecx, 0x800                       
		operands[1].type: MEM
			operands[1].mem.base: REG = rip
			operands[1].mem.disp: 0x1f462
0x1f462 128098
0x8077:	lea rsi, [rip + 0x1f462]             
0x807e:	mov rdi, rax                         
0x8081:	mov eax, 0                           
0x8086:	call 0x4b40                          
add 0x808b
0x808b:	call 0x4990                          #    if (|g|etuid() == 0)

add 0x8090
0x8090:	test eax, eax                        #    if |(|g

In [ ]:
# 0x2382a